## Importing data

In [1]:
import laspy 

In [2]:
f = laspy.file.File("./data/1_Small_clean.las")

In [3]:
colors = f.points["point"][["red", "green", "blue"]]

In [4]:
points = f.points["point"][["X", "Y", "Z"]]

In [5]:
import matplotlib.pyplot as plt

In [6]:
from sklearn.preprocessing import MinMaxScaler

In [7]:
s = MinMaxScaler()

In [8]:
import numpy as np
points = np.array(points.tolist())
colors = np.array(colors.tolist())

In [9]:
points = points / 1000

In [10]:
colors_fit = s.fit_transform(colors)

## Create voxel grid using open3d API

In [11]:
import numpy as np
import open3d as o3d

# points = (np.random.rand(1000, 3) - 0.5) / 4
# colors = np.random.rand(1000, 3)

pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(points)
pcd.colors = o3d.utility.Vector3dVector(colors_fit)


gap = 3
shift = (points[:, 0].max() - points[:, 0].min() + gap)
pcd_shifted = o3d.geometry.PointCloud()
pcd_shifted.points = o3d.utility.Vector3dVector(points + (shift, 0, 0))
pcd_shifted.colors = o3d.utility.Vector3dVector(colors_fit)


In [12]:
pcd.estimate_normals()

In [ ]:
voxel_size=0.1

In [13]:
voxel_grid = o3d.geometry.VoxelGrid.create_from_point_cloud(pcd,
                                                            voxel_size=voxel_size)

In [14]:
voxels = voxel_grid.get_voxels()

In [15]:
box_size = ((voxel_grid.get_max_bound() - voxel_grid.get_min_bound()) / voxel_size).astype(int)

### Creating mask to export voxels to trimesh in future

In [16]:
mask = np.zeros(box_size).astype(bool)

In [17]:
colors_mask = np.zeros(np.concatenate((box_size, [3])))

In [18]:
from tqdm.auto import tqdm

In [19]:
for v in tqdm(voxels):
    mask[tuple(v.grid_index)] = True
    colors_mask[tuple(v.grid_index)] = v.color

100%|██████████| 19705/19705 [00:00<00:00, 89302.61it/s]


In [20]:
o3d.visualization.draw_geometries([pcd_shifted, voxel_grid])

In [20]:
indeces_dump = np.array(list(v.grid_index[[0, 2, 1]] for v in tqdm(voxel_grid.get_voxels())))
colors_dump = np.array(list(v.color for v in tqdm(voxel_grid.get_voxels())))

100%|██████████| 19705/19705 [00:00<00:00, 394706.41it/s]


In [ ]:
np.save("indeces.npy", indeces_dump)
np.save("colors.npy", colors_dump)
np.save("bb.npy", box_size[[0, 2, 1]])

## Point cloud to mesh

In [ ]:
radii = [1]
o3d.geometry.TriangleMesh.create_from_point_cloud_ball_pivoting(pcd, radii=o3d.utility.DoubleVector(radii))

In [17]:
mesh, _ = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(pcd)

In [17]:
mesh, _ = o3d.geometry.TetraMesh.create_from_point_cloud(pcd)

In [18]:
mesh.normalize_normals()

TriangleMesh with 77950 points and 156359 triangles.

In [ ]:
o3d.io.write_triangle_mesh("alushta.stl", mesh)

In [18]:
o3d.visualization.draw_geometries([mesh], mesh_show_wireframe=False)

## Some trimesh visualizations

In [21]:
import trimesh

In [22]:
import trimesh
g = trimesh.voxel.VoxelGrid(trimesh.voxel.encoding.DenseEncoding(mask))

In [23]:
gmesh = g.as_boxes(colors=colors_mask)

In [24]:
gmesh.show()

In [54]:
data = trimesh.exchange.export.export_obj(gmesh, include_texture=False, write_texture=False)

In [47]:
trimesh.exchange.export.export_mesh()

dict_keys(['gltf_buffer_0.bin', 'gltf_buffer_1.bin', 'gltf_buffer_2.bin', 'model.gltf'])

In [55]:
with open("alushta_voxels.obj", "w") as f:
    f.write(data)
#     trimesh.exchange.export.export_mesh(gmesh, f, "o")

In [58]:
with open("alushta_points.ply", "rb") as f:
    m = trimesh.load(f, "ply")

In [60]:
data = trimesh.exchange.export.export_obj(m, include_texture=False, write_texture=False)
with open("alushta_points.obj", "w") as f:
    f.write(data)